In [1]:
#沖びき網漁業の面積を求める
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
 # あとで使うライブラリも併せて読み込み
import os
import folium
from time import sleep as slp
from selenium import webdriver
import math
import glob
import pyproj
import geopandas as gpd
from shapely.geometry import Polygon
from selenium.webdriver.chrome.options import Options
import psycopg2
connection = psycopg2.connect(host='100.83.105.131',
                              user='testuser',
                              password='testpass',
                              database='testdb')

In [2]:
#DBに入ってるデータの読み取り
day = "2022-09-30"
with connection.cursor() as cur:
    cur.execute('SELECT * FROM t1 WHERE day = %s',(day,))
    data = pd.DataFrame(cur.fetchall(), columns=[col.name for col in cur.description])
#データの整形
#　色々な都合上ここでカラム追加
data.insert(0, 'loopName',"NoName")
data.insert(0, 'color', "NoPin")

#日付と時間を結合
data['time']=data['time'].astype(str)
data['day']=data['day']+data['time']
#緯度--------------------------------------------------
#緯度を度分から度に変換

minutes = data['緯度']%100
degrees = (data['緯度']-minutes)//100
decimal_degrees = degrees + minutes/60
data['緯度']=decimal_degrees

#経度--------------------------------------------------
data.insert(0, '経度', data['軽度'])
minutes = data['経度']%100
degrees = (data['経度']-minutes)//100
decimal_degrees = degrees + minutes/60
data['経度']=decimal_degrees

data

経度  color loopName       id                 day      time  \
0     136.057117  NoPin   NoName  shiga12  2022-09-3006:05:30  06:05:30   
1     136.014300  NoPin   NoName  shiga12  2022-09-3000:13:30  00:13:30   
2     136.014300  NoPin   NoName  shiga12  2022-09-3000:14:00  00:14:00   
3     136.014300  NoPin   NoName  shiga12  2022-09-3000:14:30  00:14:30   
4     136.014300  NoPin   NoName  shiga12  2022-09-3000:15:00  00:15:00   
...          ...    ...      ...      ...                 ...       ...   
5416  136.061050  NoPin   NoName  shiga12  2022-09-3022:24:00  22:24:00   
5417  136.059450  NoPin   NoName  shiga12  2022-09-3022:24:30  22:24:30   
5418  136.058367  NoPin   NoName  shiga12  2022-09-3022:25:00  22:25:00   
5419  136.057533  NoPin   NoName  shiga12  2022-09-3022:25:30  22:25:30   
5420  136.057133  NoPin   NoName  shiga12  2022-09-3022:26:00  22:26:00   

             緯度         軽度  speed  angle  
0     35.200900  13603.427    0.0  323.0  
1     35.251517  13600.858    0.2  202.0  
2     35.251517  13600.858    0.0  202.0  
3     35.251517  13600.858    0.0  202.0  
4     35.251517  13600.858    0.4    1.0  
...         ...        ...    ...    ...  
5416  35.201183  13603.663   13.7  269.0  
5417  35.201183  13603.567    7.3  264.0  
5418  35.200900  13603.502    6.7  240.0  
5419  35.200567  13603.452    5.4  254.0  
5420  35.200833  13603.428    1.4  354.0  

[5421 rows x 10 columns]

In [3]:
id_list = data["id"].unique()
id_list

array(['shiga12', 'shiga13', 'shiga14', 'shiga15', 'shiga16', 'shiga17'],
      dtype=object)

In [4]:
# 地図に表示する色
# foliumでサポートしているのは下記19色
color_list=['red','blue','green','purple','orange','darkred','lightred','beige','darkblue','darkgreen','cadetblue','darkpurple','white','pink','lightblue','lightgreen','gray','black','lightgray']

In [5]:
# id 順日付順でソートする
data = data.sort_values(by=["id","day"])

index_data_id    =data.columns.get_loc('id')
index_data_ido   =data.columns.get_loc('緯度')
index_data_keido =data.columns.get_loc('経度')
index_data_speed =data.columns.get_loc('speed')
index_data_color =data.columns.get_loc('color')
index_data_loopName =data.columns.get_loc('loopName')



In [6]:
# 別パターン
# 0から0をすべて判定してday+id+lpoop連番をloopNameに書き込む
# loops配列を作りloopName totalDistance FLDistance(First to last Distance)　isLoopの要素を持たせる
# loops配列の中に適切な値を入れる
# totalDistanceとFLDistanceを良い感じに比較してloopしてそうなものにをTRUEにする
# (ループしているならtotalDistanceとFLDistanceにそれなりの差が出るはず)
# 　もし検出出来なければangleもみてそこそこ回転していることを検出する
# isLoopがTRUEのものだけ面積を求める
# デバックや視覚的に確認する用にisLoopがTRUEなデータだけ良い感じに変数に入れてひょうじしてもいい

loopId = id_list[0]
loopNo = 0
isLoop = True

# ここでisLoopを作ってスピードが0より多きければisLoopを1にしている
data['isloop'] = 0

def calcLoop(row):
    if row['speed'] > 0:
        row['isloop']=1
    
    return row

data = data.apply(calcLoop,axis=1)

# loopName
get_loc = data.columns.get_loc

cnt = 0
for i in range(len(data) - 1):
        if data.iloc[i,get_loc("isloop")] == 0 and data.iloc[i+1,get_loc("isloop")] == 1:
            data.iloc[i,get_loc("loopName")] = "NoLoop"
        elif data.iloc[i,get_loc("isloop")] == 1 and data.iloc[i+1,get_loc("isloop")] == 1:
            data.iloc[i,get_loc("loopName")] = day + data.iloc[i,get_loc("id")] + "loop" + str(cnt)
        elif data.iloc[i,get_loc("isloop")] == 1 and data.iloc[i+1,get_loc("isloop")] == 0:
            data.iloc[i,get_loc("loopName")] = day + data.iloc[i,get_loc("id")] + "loop" + str(cnt)
            cnt = cnt + 1
        else:
            data.iloc[i,get_loc("loopName")] = "NoLoop"

# loopごとに色をつける
data['color']="NoPin"
loop_list = data["loopName"].unique()
loop_list = loop_list[loop_list != "NoLoop"]

for idx,person in enumerate(loop_list):
    pin_color = color_list[idx%len(color_list)]
    data.loc[data["loopName"] == person, "color"] = pin_color

vc = data['loopName'].value_counts()

# 数が多すぎる少なすぎるものを削除(本来は距離でやる予定)
for idx,person in enumerate(loop_list):
    count = (data["loopName"] == person).sum()
    if count > 60 or count < 5:
        data.loc[data["loopName"] == person, "color"] = "NoPin"
        #loop_listから条件に当てはまる余分なloopNameを削除
        loop_list = loop_list[loop_list != person]

In [7]:
m = folium.Map(tiles='OpenStreetMap')
#船の航跡をidごとに色付けして表示
for idx,person in enumerate(id_list):
    # 一人分のデータだけをdataに格納する
    data_temp = data[data["id"] == person]
    
    # data_tempの順番を日時で昇順ソート
    data_temp = data_temp.sort_values('day', ascending=True)
    # print(id)
    # print(data_temp)
    # data_tempの緯度経度だけを
    data_temp_lat_lon = data_temp[["緯度","経度"]]
    
    # 緯度経度を配列に格納
    locs = data_temp_lat_lon.values
    
    # 色を指定
    line_color = color_list[idx%len(color_list)]
    
    # 地図に線を追加する。緯度経度の配列をそのまま線として使う
    folium.PolyLine(locs,color=line_color,popup=person).add_to(m)

for i in range(len(data)):
    if  data.iloc[i,index_data_color] != "NoPin":
        #print(data.iloc[i,index_data_color])
        folium.Marker(
            location = [data.iloc[i,index_data_ido],data.iloc[i,index_data_keido]],
            popup = data.iloc[i,data.columns.get_loc("loopName")],
            icon = folium.Icon(color = data.iloc[i,index_data_color])
            ).add_to(m)

m.fit_bounds([[data["緯度"].min(),data["経度"].min()], [data["緯度"].max(),data["経度"].max()]])
#m.save(day+".html")
m

In [8]:
# Start と　Endのフラグを立ててその２点間の距離を考える
# フラグ建て用のカラム「startOrend」
data["startOrend"]="Noloop"
get_loc = data.columns.get_loc
j = 0
for i in range(len(data) - 1):
    loopName = loop_list[j]
    if data.iloc[i-1,get_loc("loopName")] != loopName and data.iloc[i,get_loc("loopName")] == loopName:
        data.iloc[i,get_loc("startOrend")] = "start_" 
    if data.iloc[i,get_loc("loopName")] == loopName and data.iloc[i+1,get_loc("loopName")] != loopName:
        data.iloc[i,get_loc('startOrend')] = "end_" 
        j = j + 1

#統計用データ入れの作成
stat = pd.DataFrame()
stat["loopName"] = loop_list
stat["latS"] = None #startの座標
stat["latE"] = None #endの座標
stat["lonS"] = None
stat["lonE"] = None
stat["way"] = None #道のり
stat["distance"] = None# 距離
stat["area"] = None # 面積
#実際にデータを入れる
j = 0
for i in range(len(data) - 1):
    loopName = loop_list[j]
    #startの処理
    if data.iloc[i,get_loc("loopName")] == loopName and data.iloc[i,get_loc("startOrend")] == "start_":
        print(loopName)
        stat.loc[stat["loopName"] == loopName, "latS"] = data.iloc[i,get_loc("緯度")]
        stat.loc[stat["loopName"] == loopName, "lonS"] = data.iloc[i,get_loc("経度")]
    #endの処理
    if data.iloc[i,get_loc("loopName")] == loopName and data.iloc[i,get_loc("startOrend")] == "end_":
        print(loopName)
        stat.loc[stat["loopName"] == loopName, "latE"] = data.iloc[i,get_loc("緯度")]
        stat.loc[stat["loopName"] == loopName, "lonE"] = data.iloc[i,get_loc("経度")]
        j = j + 1
#２点間の距離を計測

# -----------------------------------------------------------
# ２点間の距離を求める関数(chatgptが教えてくれた)
# 返り値の単位はメートル
# -----------------------------------------------------------
def haversine_distance(lat1, lon1, lat2, lon2):
    #print(str(lat1)+str(lon2)+str(lat2)+str(lon2))
    # 地球の半径（平均値、単位はキロメートル）
    radius = 6371.0
    
    # 緯度経度をラジアンに変換
    lat1 = math.radians(lat1)
    lon1 = math.radians(lon1)
    lat2 = math.radians(lat2)
    lon2 = math.radians(lon2)
    
    # ハーバーシンの公式
    dlon = lon2 - lon1
    dlat = lat2 - lat1
    a = math.sin(dlat / 2)**2 + math.cos(lat1) * math.cos(lat2) * math.sin(dlon / 2)**2
    c = 2 * math.atan2(math.sqrt(a), math.sqrt(1 - a))
    
    # 距離を計算
    distance = radius * c
    
    return distance*1000

# -----------------------------------------------------------
# dfのlatとlonからいい感じに距離を求める関数
# 返り値の単位はメートル
# -----------------------------------------------------------
def haversine_way(df):
    #for i in range(len(df)-1):
    #print(df)
    #print(df)
    way = 0
    for i in range(1,len(df)):
        way = way + haversine_distance(df.iloc[i-1,0],df.iloc[i-1,1],df.iloc[i,0],df.iloc[i,1])

    #print(way)
    
    if way == 0:
         way = 0.0001
    
    return way

for i, loop in stat.iterrows():
    #print(loop)
    loop["distance"] = haversine_distance(loop["latS"], loop["lonS"], loop["latE"], loop["lonE"])

#道のりを求める
for i, loop in stat.iterrows():
    loop["way"] = haversine_way(data.loc[data["loopName"] == loop["loopName"], ["緯度","経度"]])

# 道のり引く距離が一定以下なものを非表示にする
for i, loop in stat.iterrows():
    if (  loop["distance"]/loop["way"] > 0.2):
                data.loc[data["loopName"] == loop["loopName"], "color"] = "NoPin"
                #loop_listから条件に当てはまる余分なloopNameを削除
                loop_list = loop_list[loop_list != loop["loopName"]]

2022-09-30shiga12loop1
2022-09-30shiga12loop1
2022-09-30shiga12loop2
2022-09-30shiga12loop2
2022-09-30shiga12loop5
2022-09-30shiga12loop5
2022-09-30shiga12loop8
2022-09-30shiga12loop8
2022-09-30shiga12loop10
2022-09-30shiga12loop10
2022-09-30shiga12loop11
2022-09-30shiga12loop11
2022-09-30shiga12loop13
2022-09-30shiga12loop13
2022-09-30shiga12loop14
2022-09-30shiga12loop14
2022-09-30shiga12loop22
2022-09-30shiga12loop22
2022-09-30shiga12loop24
2022-09-30shiga12loop24
2022-09-30shiga12loop25
2022-09-30shiga12loop25
2022-09-30shiga12loop26
2022-09-30shiga12loop26
2022-09-30shiga12loop27
2022-09-30shiga12loop27
2022-09-30shiga12loop28
2022-09-30shiga12loop28
2022-09-30shiga12loop30
2022-09-30shiga12loop30
2022-09-30shiga12loop31
2022-09-30shiga12loop31
2022-09-30shiga12loop36
2022-09-30shiga12loop36
2022-09-30shiga12loop37
2022-09-30shiga12loop37
2022-09-30shiga12loop42
2022-09-30shiga12loop42
2022-09-30shiga12loop45
2022-09-30shiga12loop45
2022-09-30shiga12loop46
2022-09-30shiga12loop46


In [9]:
#stat.to_excel('pandas_to_excel.xlsx', sheet_name='new_sheet_name')
m = folium.Map(tiles='OpenStreetMap')
#表示する場所
#船の航路をidごとに色付けして表示
for idx,person in enumerate(id_list):
    # 一人分のデータだけをdataに格納する
    data_temp = data[data["id"] == person]
    
    # data_tempの順番を日時で昇順ソート
    data_temp = data_temp.sort_values('day', ascending=True)
    # print(id)
    # print(data_temp)
    # data_tempの緯度経度だけを
    data_temp_lat_lon = data_temp[["緯度","経度"]]
    
    # 緯度経度を配列に格納
    locs = data_temp_lat_lon.values
    
    # 色を指定
    line_color = color_list[idx%len(color_list)]
    
    # 地図に線を追加する。緯度経度の配列をそのまま線として使う
    folium.PolyLine(locs,color=line_color,popup=person).add_to(m)

#ピンを表示
for i in range(len(data)):
    if  data.iloc[i,index_data_color] != "NoPin":
        #print(data.iloc[i,index_data_color])
        folium.Marker(
            location = [data.iloc[i,index_data_ido],data.iloc[i,index_data_keido]],
            popup = data.iloc[i,data.columns.get_loc("loopName")],
            icon = folium.Icon(color = data.iloc[i,index_data_color])
            ).add_to(m)

m.fit_bounds([[data["緯度"].min(),data["経度"].min()], [data["緯度"].max(),data["経度"].max()]])
#m.save(day+".html")
m


In [10]:
#面積を求めるコード
stat["area(m2)"] = None
def area(df ,*, latitude_column='緯度', longitude_column='経度', utm_zone=53):

    #print("area")

    coordinates = df[[latitude_column, longitude_column]].values

    # UTM座標系に変換
    utm_crs = f"+proj=utm +zone={utm_zone} +ellps=WGS84"
    project = pyproj.Transformer.from_crs(
        "EPSG:4326", utm_crs, always_xy=True).transform
    utm_coordinates = [project(lon, lat) for lat, lon in coordinates]

    # ポリゴンを作成
    coordinates = list(utm_coordinates)
    coordinates.append(coordinates[0])  # 最初と最後の座標を同じにする
    polygon = Polygon(coordinates)

    # GeoDataFrameを作成
    gdf = gpd.GeoDataFrame({'geometry': [polygon]})

    # 面積を計算
    area = gdf.area.iloc[0]

    # 面積を表示
    return area
    #print(f"ポリゴンの面積 (UTM座標系): {area} 平方メートル")

#花弁ごとの面積
for i, loop in stat.iterrows():
    #print(data[data["loopName"] == loop["loopName"]])
    loop["area(m2)"] = area(data[data["loopName"] == loop["loopName"]])

#航路ごとの面積
ship = pd.DataFrame()
ship["id"] = id_list
ship["area(m2)"] = 0
for idx, id in enumerate(id_list):
    df = stat[stat["loopName"].str.contains(id)]
    sum = df["area(m2)"].sum()
    ship.loc[ship["id"] == id, 'area(m2)'] = sum
    print(sum)

#面でき求めるときに使ったデータの出力
# 一人分のデータだけをdataに格納する
id = "shiga17"
data_out = data[data["id"] == id]
data_out = data_out[data_out["color"] != "NoPin"]
data_out = data_out[["経度", "緯度"]]
data_out.to_csv("output\{}.csv".format(id), index=False)


    


12378465.525083235
229442.99522573498
608986.0307840811
142241.91394907518
305515.78398400755
645766.5128164233


In [11]:
#DBに入れる